In [35]:
import pandas as pd
from shapely.geometry import Point, Polygon, MultiPolygon, shape, GeometryCollection, shape
import shapely.ops
import json
import pyproj
from functools import partial
import geopandas as gpd

In [2]:
df = pd.read_csv(r'..\..\data\nypp.csv')

In [3]:
df

Precinct                                           the_geom    Shape_Area  \
0          1  MULTIPOLYGON (((-74.0438776157395 40.690187676...  4.731472e+07   
1          5  MULTIPOLYGON (((-73.98863862848766 40.72293372...  1.808880e+07   
2          6  MULTIPOLYGON (((-73.99968392160721 40.73855224...  2.209819e+07   
3         71  MULTIPOLYGON (((-73.92854313809303 40.66457328...  4.533179e+07   
4         72  MULTIPOLYGON (((-73.99840899113158 40.67186872...  1.046213e+08   
..       ...                                                ...           ...   
72       115  MULTIPOLYGON (((-73.85907893495997 40.76252283...  1.133427e+08   
73       120  MULTIPOLYGON (((-74.05356753570328 40.60369646...  2.323947e+08   
74       121  MULTIPOLYGON (((-74.15945602438185 40.64144833...  4.756924e+08   
75       122  MULTIPOLYGON (((-74.05050806403284 40.56642203...  4.547993e+08   
76       123  MULTIPOLYGON (((-74.1698265639346 40.561078003...  4.608700e+08   

       Shape_Leng  
0    80797.248793  
1    18676.124259  
2    26402.900669  
3    29978.094261  
4    87968.194520  
..            ...  
72   60051.601409  
73   92981.054897  
74  136834.152032  
75  154881.006310  
76  120830.181066  

[77 rows x 4 columns]

In [64]:
df.dtypes

Precinct        int64
the_geom       object
Shape_Area    float64
Shape_Leng    float64
dtype: object

In [36]:
#testing
#this point should be within Precint 5
p1 = Point(-73.99586, 40.72521)

In [62]:
#(-73.98863862848766 40.72293372026369, -73.98868690007737 40.72285731808216, -73.98877533267515 40.7226156968876, -73.9888936174098 40.7222925092235, -73.98894819277763 40.7221433918762, -73.98898560733659 40.72204116527433, -73.98913063635348 40.721644897853736, -73.98972000121199 40.72047858431298, -73.9903231261167 40.71928036425406, -73.99036354389418 40.71920481539384, -73.99040724131198 40.71912093585063, -73.99084515016456 40.71830857660505, -73.99130415370982 40.71738168193542, -73.99167727171255 40.71665064001351, -73.99172724143197 40.716552735713925, -73.99190572915857 40.71620302145721, -73.99249062534805 40.71508034087649, -73.99270089449267 40.714651818703395, -73.99282173481265 40.714365229949685, -73.99272266354569 40.71384440460542, -73.99258219677559 40.71375671371465, -73.9925006149871 40.71317957960038, -73.99240212650656 40.71246237061515, -73.9923904010968 40.71236250718046, -73.9923883267743 40.71234483847608, -73.99238164874323 40.712287957768474, -73.99237819491961 40.71225854147838, -73.99235432176475 40.71205520670713, -73.99234226717795 40.71195308882971, -73.99232017166835 40.71176433487263, -73.99230590945655 40.7116925320213, -73.99229297111606 40.71162811987681, -73.99228302144793 40.71155234072184, -73.99215370614098 40.711074741664895, -73.99211109553504 40.710988256790976, -73.99208823903524 40.71090341184129, -73.99201913025111 40.71059030931124, -73.99185852715475 40.709808025281696, -73.99190709798711 40.70980199354539, -73.99187980258947 40.7097548530351, -73.9918590272103 40.70971897213604, -73.99182888067827 40.709666524657685, -73.99179955131694 40.70961115957848, -73.99178277805896 40.70958152603311, -73.99178002939966 40.70957666922814, -73.99176779580138 40.70955505502111, -73.99190544366458 40.709525396079655, -73.99203926968352 40.70951691916273, -73.99209131635973 40.70950822240118, -73.9921486897015 40.70949860910409, -73.99236116139905 40.709464369314006, -73.99284846748647 40.70938187763873, -73.99374012862224 40.709246120937905, -73.99400820164043 40.70923748042158, -73.99414063200345 40.70923326739993, -73.99437823543936 40.70919263919891, -73.99457899963724 40.70913097291005, -73.99517577369834 40.70903429381029, -73.99580385653569 40.708946013907486, -73.99601898395763 40.70891622384743, -73.9966640099659 40.7088269045177, -73.99728287195578 40.7087316198429, -73.99808351186999 40.708509615367134, -73.99828602320592 40.70842993146759, -73.99852758585311 40.70833152790828, -73.99856114620617 40.70831528273096, -73.99872197955064 40.708237452896164, -73.99875396570859 40.70822365152976, -73.99880846276645 40.70820013449007, -73.99882158420985 40.70817548117489, -73.9988813086388 40.708136633919786, -73.99898340963244 40.708092653316136, -73.99905276738552 40.70803254536376, -73.9991343491895 40.707982397448504, -73.99919451108852 40.70794737635147, -73.99925945470771 40.7079140213104, -73.99932632675426 40.707879676493924, -73.99938225243403 40.707841549321515, -73.99942129138608 40.70781893705531, -73.99946033075193 40.707796325948486, -73.9995232500711 40.70776262865813, -73.99951211430798 40.70774870660909, -73.99949062474623 40.70772184472241, -73.99953839725494 40.70769347002567, -73.99955121325496 40.7076943527765, -73.9995714951379 40.70771719818587, -73.99960249674827 40.707752108258866, -73.99960948105294 40.70775997317629, -73.9998829708522 40.7076240860353, -73.99989574568755 40.707617737944084, -73.9999588166742 40.70768818345429, -74.00003379419385 40.707806799995986, -74.00007514781151 40.70784723531564, -74.00013109195302 40.707913267233124, -74.0004835408566 40.708350862733916, -74.0008601109041 40.70879094707493, -74.00166466865358 40.70952276305005, -74.00210952706912 40.709893912898835, -74.00308193099914 40.71062428716192, -74.0031563339572 40.71067297502858, -74.00338054973804 40.710826163734744, -74.00343203072377 40.71087981407516, -74.00355036463868 40.71097316641705, -74.00361454307568 40.71100834793827, -74.0038527832684 40.71114209309843, -74.00391102115795 40.71117478838408, -74.00425246221761 40.71138934083344, -74.00443160395999 40.71151306415221, -74.0049916384807 40.71188096282683, -74.0050516064839 40.71192812073176, -74.00512487522043 40.711965488072096, -74.00520688890471 40.711990176696055, -74.00529195450655 40.71200097897737, -74.00566290071504 40.71198231557449, -74.00573499331394 40.71197868839692, -74.00589175101486 40.71200715956491, -74.00574044668751 40.71208875703634, -74.00558932954131 40.71217005375554, -74.0054581989065 40.71219782496352, -74.00543047939837 40.71220369524702, -74.00527561958643 40.712249439992746, -74.00512712618752 40.71230677325996, -74.0049871665652 40.71237485717677, -74.00485768087732 40.71245254111691, -74.00460261285207 40.71265752000517, -74.00429113891556 40.712907825695886, -74.00421405367503 40.712980742642195, -74.00405900803744 40.71313479025531, -74.00481860655783 40.713475000498775, -74.00630969599493 40.71416582661869, -74.00588849736322 40.71467728518714, -74.00541948410378 40.71523605705498, -74.00497612896957 40.715759939895534, -74.00453350110088 40.71627991256102, -74.00419822714433 40.71667044970024, -74.00402602619415 40.716871017684575, -74.00353244739755 40.717449430609264, -74.00304533455166 40.71802581664014, -74.00253798721954 40.71862688357911, -74.00209161668549 40.71915339284899, -74.00188406309478 40.71939757028781, -74.0014245100964 40.719937198165916, -74.00066072523035 40.720839794377795, -73.99985330434208 40.72179178766753, -73.99952163175969 40.72218334688825, -73.99881172246083 40.72302140919117, -73.99778508864233 40.724234894250735, -73.99684295933554 40.725347837869776, -73.99677175777505 40.72543194350264, -73.9958457755858 40.72520835348177, -73.99532907937457 40.72508373972877, -73.99490827388995 40.72495122921941, -73.99417930485532 40.724692406811606, -73.9934576909809 40.724432895683286, -73.99339891296906 40.724412504831434, -73.99267182446474 40.72416025442204, -73.99260322264499 40.724136449683435, -73.99250385902864 40.72410592541924, -73.99135472800884 40.72375461908481, -73.99127307162458 40.72372981293941, -73.99111507481845 40.723678802707006, -73.99102410461465 40.72364943223782, -73.99099736302554 40.72364147145813, -73.99027361647936 40.72342601779058, -73.98939218169832 40.72317405849503, -73.98875683260616 40.72297036611113, -73.98863862848766 40.72293372026369)

coords = [
    (-73.98863862848766, 40.72293372026369), 
    (-73.98868690007737, 40.72285731808216), 
    (-73.98877533267515, 40.7226156968876), 
    (-73.9888936174098, 40.7222925092235), 
    (-73.98894819277763, 40.7221433918762), 
    (-73.98898560733659, 40.72204116527433), 
    (-73.98913063635348, 40.721644897853736), 
    (-73.98972000121199, 40.72047858431298), 
    (-73.9903231261167, 40.71928036425406), 
    (-73.99036354389418, 40.71920481539384), 
    (-73.99040724131198, 40.71912093585063), 
    (-73.99084515016456, 40.71830857660505), 
    (-73.99130415370982, 40.71738168193542), 
    (-73.99167727171255, 40.71665064001351), 
    (-73.99172724143197, 40.716552735713925), 
    (-73.99190572915857, 40.71620302145721), 
    (-73.99249062534805, 40.71508034087649), 
    (-73.99270089449267, 40.714651818703395), 
    (-73.99282173481265, 40.714365229949685), 
    (-73.99272266354569, 40.71384440460542), 
    (-73.99258219677559, 40.71375671371465), 
    (-73.9925006149871, 40.71317957960038), 
    (-73.99240212650656, 40.71246237061515), 
    (-73.9923904010968, 40.71236250718046), 
    (-73.9923883267743, 40.71234483847608),
    (-73.99238164874323, 40.712287957768474), 
    (-73.99237819491961, 40.71225854147838), 
    (-73.99235432176475, 40.71205520670713),
 	(-73.99234226717795, 40.71195308882971),
 	(-73.99232017166835, 40.71176433487263),
 	(-73.99230590945655, 40.7116925320213),
 	(-73.99229297111606, 40.71162811987681),
 	(-73.99228302144793, 40.71155234072184),
 	(-73.99215370614098, 40.711074741664895),
 	(-73.99211109553504, 40.710988256790976),
 	(-73.99208823903524, 40.71090341184129),
 	(-73.99201913025111, 40.71059030931124),
 	(-73.99185852715475, 40.709808025281696),
 	(-73.99190709798711, 40.70980199354539),
 	(-73.99187980258947, 40.7097548530351),
 	(-73.9918590272103, 40.70971897213604),
 	(-73.99182888067827, 40.709666524657685),
 	(-73.99179955131694, 40.70961115957848),
 	(-73.99178277805896, 40.70958152603311),
 	(-73.99178002939966, 40.70957666922814),
 	(-73.99176779580138, 40.70955505502111),
 	(-73.99190544366458, 40.709525396079655),
 	(-73.99203926968352, 40.70951691916273),
 	(-73.99209131635973, 40.70950822240118),
 	(-73.9921486897015, 40.70949860910409),
 	(-73.99236116139905, 40.709464369314006),
 	(-73.99284846748647, 40.70938187763873),
 	(-73.99374012862224, 40.709246120937905),
 	(-73.99400820164043, 40.70923748042158),
 	(-73.99414063200345, 40.70923326739993),
 	(-73.99437823543936, 40.70919263919891),
 	(-73.99457899963724, 40.70913097291005),
 	(-73.99517577369834, 40.70903429381029),
 	(-73.99580385653569, 40.708946013907486),
 	(-73.99601898395763, 40.70891622384743),
 	(-73.9966640099659, 40.7088269045177),
 	(-73.99728287195578, 40.7087316198429),
 	(-73.99808351186999, 40.708509615367134),
 	(-73.99828602320592, 40.70842993146759),
 	(-73.99852758585311, 40.70833152790828),
 	(-73.99856114620617, 40.70831528273096),
 	(-73.99872197955064, 40.708237452896164),
 	(-73.99875396570859, 40.70822365152976),
 	(-73.99880846276645, 40.70820013449007),
 	(-73.99882158420985, 40.70817548117489),
 	(-73.9988813086388, 40.708136633919786),
 	(-73.99898340963244, 40.708092653316136),
 	(-73.99905276738552, 40.70803254536376),
 	(-73.9991343491895, 40.707982397448504),
 	(-73.99919451108852, 40.70794737635147),
 	(-73.99925945470771, 40.7079140213104),
 	(-73.99932632675426, 40.707879676493924),
 	(-73.99938225243403, 40.707841549321515),
 	(-73.99942129138608, 40.70781893705531),
 	(-73.99946033075193, 40.707796325948486),
 	(-73.9995232500711, 40.70776262865813),
 	(-73.99951211430798, 40.70774870660909),
 	(-73.99949062474623, 40.70772184472241),
 	(-73.99953839725494, 40.70769347002567),
 	(-73.99955121325496, 40.7076943527765),
 	(-73.9995714951379, 40.70771719818587),
 	(-73.99960249674827, 40.707752108258866),
 	(-73.99960948105294, 40.70775997317629),
 	(-73.9998829708522, 40.7076240860353),
 	(-73.99989574568755, 40.707617737944084),
 	(-73.9999588166742, 40.70768818345429),
 	(-74.00003379419385, 40.707806799995986),
 	(-74.00007514781151, 40.70784723531564),
 	(-74.00013109195302, 40.707913267233124),
 	(-74.0004835408566, 40.708350862733916),
 	(-74.0008601109041, 40.70879094707493),
 	(-74.00166466865358, 40.70952276305005),
 	(-74.00210952706912, 40.709893912898835),
 	(-74.00308193099914, 40.71062428716192),
 	(-74.0031563339572, 40.71067297502858),
 	(-74.00338054973804, 40.710826163734744),
 	(-74.00343203072377, 40.71087981407516),
 	(-74.00355036463868, 40.71097316641705),
 	(-74.00361454307568, 40.71100834793827),
 	(-74.0038527832684, 40.71114209309843),
 	(-74.00391102115795, 40.71117478838408),
 	(-74.00425246221761, 40.71138934083344),
 	(-74.00443160395999, 40.71151306415221),
 	(-74.0049916384807, 40.71188096282683),
 	(-74.0050516064839, 40.71192812073176),
 	(-74.00512487522043, 40.711965488072096),
 	(-74.00520688890471, 40.711990176696055),
 	(-74.00529195450655, 40.71200097897737),
 	(-74.00566290071504, 40.71198231557449),
 	(-74.00573499331394, 40.71197868839692),
 	(-74.00589175101486, 40.71200715956491),
 	(-74.00574044668751, 40.71208875703634),
 	(-74.00558932954131, 40.71217005375554),
 	(-74.0054581989065, 40.71219782496352),
 	(-74.00543047939837, 40.71220369524702),
 	(-74.00527561958643, 40.712249439992746),
 	(-74.00512712618752, 40.71230677325996),
 	(-74.0049871665652, 40.71237485717677),
 	(-74.00485768087732, 40.71245254111691),
 	(-74.00460261285207, 40.71265752000517),
 	(-74.00429113891556, 40.712907825695886),
 	(-74.00421405367503, 40.712980742642195),
 	(-74.00405900803744, 40.71313479025531),
 	(-74.00481860655783, 40.713475000498775),
 	(-74.00630969599493, 40.71416582661869),
 	(-74.00588849736322, 40.71467728518714),
 	(-74.00541948410378, 40.71523605705498),
 	(-74.00497612896957, 40.715759939895534),
 	(-74.00453350110088, 40.71627991256102),
 	(-74.00419822714433, 40.71667044970024),
 	(-74.00402602619415, 40.716871017684575),
 	(-74.00353244739755, 40.717449430609264),
 	(-74.00304533455166, 40.71802581664014),
 	(-74.00253798721954, 40.71862688357911),
 	(-74.00209161668549, 40.71915339284899),
 	(-74.00188406309478, 40.71939757028781),
 	(-74.0014245100964, 40.719937198165916),
 	(-74.00066072523035, 40.720839794377795),
 	(-73.99985330434208, 40.72179178766753),
 	(-73.99952163175969, 40.72218334688825),
 	(-73.99881172246083, 40.72302140919117),
 	(-73.99778508864233, 40.724234894250735),
 	(-73.99684295933554, 40.725347837869776),
 	(-73.99677175777505, 40.72543194350264),
 	(-73.9958457755858, 40.72520835348177),
 	(-73.99532907937457, 40.72508373972877),
 	(-73.99490827388995, 40.72495122921941),
 	(-73.99417930485532, 40.724692406811606),
 	(-73.9934576909809, 40.724432895683286),
 	(-73.99339891296906, 40.724412504831434),
 	(-73.99267182446474, 40.72416025442204),
 	(-73.99260322264499, 40.724136449683435),
 	(-73.99250385902864, 40.72410592541924),
 	(-73.99135472800884, 40.72375461908481),
 	(-73.99127307162458, 40.72372981293941),
 	(-73.99111507481845, 40.723678802707006),
 	(-73.99102410461465, 40.72364943223782),
 	(-73.99099736302554, 40.72364147145813),
 	(-73.99027361647936, 40.72342601779058),
 	(-73.98939218169832, 40.72317405849503),
 	(-73.98875683260616, 40.72297036611113),
 	(-73.98863862848766, 40.72293372026369)
 ]

polygon_precinct_5 = Polygon(coords)

In [63]:
#yay it works!!!, but it'll take me ages to do this via CSV
p1.within(polygon_precinct_5)

True

In [17]:
with open("..\..\data\Police Precincts.geojson") as f:
  features = json.load(f)["features"]

In [18]:
features

[{'type': 'Feature',
  'properties': {'precinct': '1',
   'shape_area': '47314724.6545',
   'shape_leng': '80797.2487935'},
  'geometry': {'type': 'MultiPolygon',
   'coordinates': [[[[-74.0438776157395, 40.69018767637665],
      [-74.0435059601254, 40.68968735963635],
      [-74.04273533826982, 40.69005019142044],
      [-74.04278433380006, 40.69012097669115],
      [-74.04270428426766, 40.690155204644306],
      [-74.04255372037308, 40.6899627592896],
      [-74.0426392937119, 40.68992817641333],
      [-74.0426938081918, 40.689997259107216],
      [-74.04346752310265, 40.68963699010347],
      [-74.04351637245855, 40.68919103374234],
      [-74.04364078627412, 40.68876655957014],
      [-74.04397458556184, 40.68858240705591],
      [-74.0443852177728, 40.688516178402686],
      [-74.04478399040363, 40.68859566011588],
      [-74.04627539003668, 40.689327425896714],
      [-74.04680284898575, 40.68995325626601],
      [-74.04747651462345, 40.68961136999828],
      [-74.04772962763064

In [28]:
geometry = GeometryCollection([shape(feature["geometry"]).buffer(0) for feature in features])
geometry

In [29]:
# Suppose geometry is an instance of shapely.geometry.Geometry
tfm = partial(pyproj.transform, 
              pyproj.Proj(init="epsg:4326"), 
              pyproj.Proj(init="epsg:3031"))
reprojected = shapely.ops.transform(tfm, geometry)

c:\users\alexf\anaconda3\envs\nyc_crash_env\lib\site-packages\pyproj\crs.py:77: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method.
  return _prepare_from_string(" ".join(pjargs))
c:\users\alexf\anaconda3\envs\nyc_crash_env\lib\site-packages\pyproj\crs.py:77: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method.
  return _prepare_from_string(" ".join(pjargs))


In [32]:
precincts =  gpd.read_file('..\..\data\Police Precincts.geojson')

In [101]:
precincts

precinct     shape_area     shape_leng  \
0         1  47314724.6545  80797.2487935   
1         5  18088797.9526  18676.1242594   
2         6  22098189.8026  26402.9006691   
3        71  45331787.1744  29978.0942611   
4        72  104621257.743  87968.1945199   
..      ...            ...            ...   
72      115  113342670.866   60051.601409   
73      120  232394745.247  92981.0548968   
74      121   475692409.26  136834.152032   
75      122  454799251.518   154881.00631   
76      123  460870016.224  120830.181066   

                                             geometry  
0   MULTIPOLYGON (((-74.04388 40.69019, -74.04351 ...  
1   MULTIPOLYGON (((-73.98864 40.72293, -73.98869 ...  
2   MULTIPOLYGON (((-73.99968 40.73855, -73.99684 ...  
3   MULTIPOLYGON (((-73.92854 40.66457, -73.92872 ...  
4   MULTIPOLYGON (((-73.99841 40.67187, -73.99830 ...  
..                                                ...  
72  MULTIPOLYGON (((-73.85908 40.76252, -73.85943 ...  
73  MULTIPOLYGON (((-74.05357 40.60370, -74.05407 ...  
74  MULTIPOLYGON (((-74.15946 40.64145, -74.15975 ...  
75  MULTIPOLYGON (((-74.05051 40.56642, -74.05047 ...  
76  MULTIPOLYGON (((-74.16983 40.56108, -74.16974 ...  

[77 rows x 4 columns]

In [102]:
type(precincts)

geopandas.geodataframe.GeoDataFrame

In [58]:
precincts.dtypes

precinct        object
shape_area      object
shape_leng      object
geometry      geometry
dtype: object

In [34]:
precincts.geometry

0     MULTIPOLYGON (((-74.04388 40.69019, -74.04351 ...
1     MULTIPOLYGON (((-73.98864 40.72293, -73.98869 ...
2     MULTIPOLYGON (((-73.99968 40.73855, -73.99684 ...
3     MULTIPOLYGON (((-73.92854 40.66457, -73.92872 ...
4     MULTIPOLYGON (((-73.99841 40.67187, -73.99830 ...
                            ...                        
72    MULTIPOLYGON (((-73.85908 40.76252, -73.85943 ...
73    MULTIPOLYGON (((-74.05357 40.60370, -74.05407 ...
74    MULTIPOLYGON (((-74.15946 40.64145, -74.15975 ...
75    MULTIPOLYGON (((-74.05051 40.56642, -74.05047 ...
76    MULTIPOLYGON (((-74.16983 40.56108, -74.16974 ...
Name: geometry, Length: 77, dtype: geometry

In [50]:
fifth_precinct = precincts.loc[precincts.precinct == '5']

In [69]:
fifth_precinct['geometry'].geom_type
#fifth_precinct_polygon = shape(fifth_precinct['geometry'])

1    MultiPolygon
dtype: object

In [84]:
fifth_precinct['geometry'].geom_type == 'MultiPolygon'

1    True
dtype: bool

In [93]:
for polygon in fifth_precinct.geometry:
    mp = MultiPolygon(polygon)
    print(p1.within(mp))

True


In [107]:
for index, precinct in precincts.iterrows():
    #print(precinct)
    mp = MultiPolygon(precinct.geometry)
    if p1.within(mp):
        print(' the point fits! ')
        print(' at precinct: ' + precinct['precinct'])
    

 the point fits! 
 at precinct: 5
